# Pump It Up

## High Level Description

This code was developed as part of the [Pump It Up Competition](https://www.drivendata.org/competitions/7/pump-it-up-data-mining-the-water-table/page/23/), on DrivenData. The goal of this ML project is to promote access to clean and portable water accross Tanzania. 

The model being developed is an ensemble model, utilizing XGBoost, and CatBoost.

The final ML model will predict whether water pumps should be labelled as "functional", "functional needs repair", or "non functional".  

## Table of Contents
1. [Import and Setup](#import-and-setup)
2. [Data Cleaning and Feature Engineering](#data-cleaning--feature-engineering)
3. [Convert Data Types](#convert-data-types)
4. [Training and Hpyerparameter Tuning](#training-and-hyperparameter-tuning)
   1. [Random Forest](#random-forest)
   2. [XGBoost](#xgboost)
   3. [CatBoost](#catboost)
5. [Ensemble Voting](#ensemble-voting)

### Import and Setup
Import the standard python libraries and datasets.

To download a copy of the dataset for yourself, please sign up for the [Pump It Up Competition](https://www.drivendata.org/competitions/7/pump-it-up-data-mining-the-water-table/page/23/) on DrivenData, and download it for free.

In [43]:
import numpy as np
import pandas as pd
import HelperFunctions

In [44]:
xtrain = pd.read_csv(r'D:\MMAI\Pump-It-Up\data\x_train.csv')
xtest = pd.read_csv(r'D:\MMAI\Pump-It-Up\data\x_test.csv')
ytrain = pd.read_csv(r'D:\MMAI\Pump-It-Up\data\y_train.csv')
raw = pd.concat([xtrain, xtest])

In [45]:
del ytrain['id']

### Data Cleaning & Feature Engineering

In [46]:
# cleanup - make sure everything is lowercase
raw = HelperFunctions.toLowerCase(raw)

In [47]:
# FE - Handle DateType variables
# Convert date into year, month, and days since recorded

def fixDates(df):
    df['date_recorded'] = pd.to_datetime(df['date_recorded'])
    df['year_recorded'] = (df['date_recorded'].dt.year).astype('int')
    df['month_recorded'] = (df['date_recorded'].dt.month).astype('str')
    df['days_since_recorded'] = ((pd.to_datetime('2001-03-26') - df['date_recorded']).dt.days).astype('int')
    del df['date_recorded']
    return df

xtrain = fixDates(xtrain)
xtest = fixDates(xtest)
raw = fixDates(raw)

In [48]:
# Impute 'longitude' based on subvillage, ward, lga, region
raw = HelperFunctions.imputeLong(raw)

# Impute 'permit' based on subvillage, ward, lga, region
permit_geo_mode = raw.groupby(['subvillage', 'ward', 'lga', 'region'])['permit'].agg(pd.Series.mode).reset_index()
permit_geo_mode = permit_geo_mode.rename(columns={"permit": "imputed_permit_geo"})
raw = raw.merge(permit_geo_mode, how='left', on=['subvillage', 'ward', 'lga', 'region'])
raw['imputed_permit'] = np.where(raw['permit'].isna(), raw['imputed_permit_geo'], raw['permit'])
raw['imputed_permit'] = np.where(raw['imputed_permit'].isna(), raw['permit'].mode()[0], raw['imputed_permit'])
raw = raw.drop(['permit', 'imputed_permit_geo'], axis=1)

# Impute 'population' based on subvillage, ward, lga, region
population_geo_mode = raw.groupby(['subvillage', 'ward', 'lga', 'region'])['population'].agg(pd.Series.mode).reset_index()
population_geo_mode = population_geo_mode.rename(columns={"population": "imputed_population_geo"})
raw = raw.merge(population_geo_mode, how='left', on=['subvillage', 'ward', 'lga', 'region'])
raw['imputed_population'] = np.where(raw['population'].isna(), raw['imputed_population_geo'], raw['population'])
raw['imputed_population'] = np.where(raw['imputed_population'].isna(), raw['population'].mode()[0], raw['imputed_population'])
raw = raw.drop(['population', 'imputed_population_geo'], axis=1)

# Impute 'gps_height' based on basin, subvillage, ward, lga, region
gps_height_geo_mode = raw.groupby(['basin', 'subvillage', 'ward', 'lga', 'region'])['gps_height'].agg(pd.Series.mode).reset_index()
gps_height_geo_mode = gps_height_geo_mode.rename(columns={"gps_height": "imputed_gps_height_geo"})
raw = raw.merge(gps_height_geo_mode, how='left', on=['basin','subvillage', 'ward', 'lga', 'region'])
raw['imputed_gps_height'] = np.where(raw['gps_height'].isna(), raw['imputed_gps_height_geo'], raw['gps_height'])
raw['imputed_gps_height'] = np.where(raw['imputed_gps_height'].isna(), raw['gps_height'].mode()[0], raw['imputed_gps_height'])
raw = raw.drop(['gps_height', 'imputed_gps_height_geo'], axis=1)

# Impute public meeting based on mode
raw['public_meeting']=raw['public_meeting'].fillna(raw['public_meeting'].mode()[0])

# Impute construction_year by mode
raw['construction_year'] = raw['construction_year'].fillna(raw['construction_year'].mode()[0])




In [49]:
# FE - Binning
# Group columns with high feature cardinality

cols = [i for i in raw.columns if type(raw[i].iloc[0]) == str]
raw[cols] = raw[cols].where(raw[cols].apply(lambda x: x.map(x.value_counts())) > 100, "other")
for column in cols:
    for i in raw[column].unique():
        if i not in raw[column].unique():
            raw[column].replace(i, 'other', inplace=True)

In [50]:
# Cleanup - Drop columns that are poorly distributed or have high co-linearity

# Poorly distributed
xtrain, xtest = HelperFunctions.removeCol(xtrain, xtest, 'amount_tsh')
xtrain, xtest = HelperFunctions.removeCol(xtrain, xtest, 'wpt_name')
xtrain, xtest = HelperFunctions.removeCol(xtrain, xtest, 'num_private')

# High co-linearity
xtrain, xtest = HelperFunctions.removeCol(xtrain, xtest, 'quantity_group')
xtrain, xtest = HelperFunctions.removeCol(xtrain, xtest, 'region')
xtrain, xtest = HelperFunctions.removeCol(xtrain, xtest, 'waterpoint_type_group')
xtrain, xtest = HelperFunctions.removeCol(xtrain, xtest, 'extraction_type_group')
xtrain, xtest = HelperFunctions.removeCol(xtrain, xtest, 'source_type')


### Convert Data Types

In [51]:

#replace string to integer
raw['public_meeting'] = raw['public_meeting'].replace({True: 1, False: 0})
raw['imputed_permit'] = raw['imputed_permit'].apply(lambda x: 0 if isinstance(x, list) and not x else x)
raw['imputed_permit'] = raw['imputed_permit'].apply(lambda x: x if x in [True, False] else 0)
raw['imputed_permit'] = raw['imputed_permit'].replace({True: 1, False: 0})


#change to integer
raw[['imputed_gps_height', 'construction_year', 'imputed_population']] = raw[['imputed_gps_height', 'construction_year', 'imputed_population']].astype('int')

#change type to categorical
raw[[ 'region_code', 'district_code', 'num_private']] = raw[[ 'region_code', 'district_code', 'num_private']].astype('str')

#remove decimal
raw['district_code'] = raw['district_code'].str.split(".").str[0]

raw= raw.rename(columns={"imputed_permit": "permit",
                    "imputed_gps_height": "gps_height", 
                   'imputed_population': 'population', 'imputed_longitude': 'longitude'}, errors="raise")


C:\Users\Namsi\AppData\Local\Temp\ipykernel_11484\2797745619.py:4: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  raw['imputed_permit'] = raw['imputed_permit'].apply(lambda x: x if x in [True, False] else 0)


In [52]:
del raw['amount_tsh']
del raw['wpt_name']
del raw['num_private']
del raw['quantity_group']
del raw['region']
del raw['waterpoint_type_group']
del raw['extraction_type_group']
del raw['source_type']


In [53]:
raw.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 74250 entries, 0 to 74249
Data columns (total 34 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   id                     74250 non-null  int64  
 1   funder                 74250 non-null  object 
 2   installer              74250 non-null  object 
 3   latitude               74250 non-null  float64
 4   basin                  74250 non-null  object 
 5   subvillage             74250 non-null  object 
 6   region_code            74250 non-null  object 
 7   district_code          74250 non-null  object 
 8   lga                    74250 non-null  object 
 9   ward                   74250 non-null  object 
 10  public_meeting         74250 non-null  int64  
 11  recorded_by            74250 non-null  object 
 12  scheme_management      74250 non-null  object 
 13  scheme_name            74250 non-null  object 
 14  construction_year      74250 non-null  int32  
 15  ex

In [54]:
x_train = raw[raw['id'].isin(xtrain['id'])]
x_test = raw[raw['id'].isin(xtest['id'])]
del x_train['id']
del x_test['id']

In [55]:
def oneHotEncoding(X_train, X_test):
    columns = [i for i in X_train.columns if type(X_train[i].iloc[0]) == str]
    for column in columns:
        X_train[column].fillna('NULL', inplace = True)
        good_cols = [column+'_'+i for i in X_train[column].unique() if i in X_test[column].unique()]
        X_train = pd.concat((X_train, pd.get_dummies(X_train[column], prefix = column)[good_cols]), axis = 1)
        X_test = pd.concat((X_test, pd.get_dummies(X_test[column], prefix = column)[good_cols]), axis = 1)
        del X_train[column]
        del X_test[column]
    return X_train, X_test

x_train, x_test = oneHotEncoding(x_train, x_test)

C:\Users\Namsi\AppData\Local\Temp\ipykernel_11484\3396669489.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  X_train[column].fillna('NULL', inplace = True)


### Training and Hyperparameter Tuning

Trained and tested the following Models: Random Forest, XGBoost, LGBM, CatBoost. Hypertuned with Optuna.

In [56]:
from sklearn.model_selection import train_test_split

x_train, x_validate, y_train, y_validate = train_test_split(x_train, ytrain, test_size=0.2, random_state=42)

#### Random Forest

In [15]:
import optuna
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import cross_val_score

rf = RandomForestClassifier(criterion='gini',
                                max_features='sqrt',
                                min_samples_split=6,
                                oob_score=True,
                                random_state=1,
                                n_jobs=-1)

# param_grid = {"n_estimators" : [500, 750, 1000]}
# param_grid = {"n_estimators" : [1000]}

def objective(trial):
    criterion = trial.suggest_categorical('criterion', ['gini'])
    n_estimators = 700
    # n_estimators = trial.suggest_int('n_estimators', 500, 1500)
    max_depth = trial.suggest_int('max_depth', 10, 100, 10)
    min_samples_split = trial.suggest_int('min_samples_split', 2, 40)
    max_features = trial.suggest_categorical('max_features', ['sqrt'])

    clf = RandomForestClassifier(
        n_estimators=n_estimators, 
        max_depth=max_depth, 
        min_samples_split=min_samples_split,
        max_features=max_features,
        random_state=42
    )
    
    return cross_val_score(clf, x_train, ytrain.values.ravel(), cv=5, scoring='accuracy', verbose=1, error_score='raise', n_jobs=-2).mean()

study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=5, n_jobs=-1)

print('Best trial: score {}, params {}'.format(study.best_trial.value, study.best_trial.params))

[I 2024-09-25 15:03:34,261] A new study created in memory with name: no-name-363fa0a7-5146-42cb-ab98-2c50542c068b
[Parallel(n_jobs=-2)]: Using backend LokyBackend with 11 concurrent workers.
[Parallel(n_jobs=-2)]: Using backend LokyBackend with 11 concurrent workers.
[Parallel(n_jobs=-2)]: Using backend LokyBackend with 11 concurrent workers.
[Parallel(n_jobs=-2)]: Using backend LokyBackend with 11 concurrent workers.
[Parallel(n_jobs=-2)]: Using backend LokyBackend with 11 concurrent workers.
[Parallel(n_jobs=-2)]: Using backend LokyBackend with 11 concurrent workers.
[Parallel(n_jobs=-2)]: Using backend LokyBackend with 11 concurrent workers.
[Parallel(n_jobs=-2)]: Using backend LokyBackend with 11 concurrent workers.
[Parallel(n_jobs=-2)]: Using backend LokyBackend with 11 concurrent workers.
[Parallel(n_jobs=-2)]: Using backend LokyBackend with 11 concurrent workers.
[Parallel(n_jobs=-2)]: Using backend LokyBackend with 11 concurrent workers.
[Parallel(n_jobs=-2)]: Using backend Lo

Best trial: score 0.8095117845117846, params {'criterion': 'gini', 'max_depth': 80, 'min_samples_split': 12, 'max_features': 'sqrt'}


In [39]:
from sklearn.metrics import accuracy_score
top_params = study.best_params

# Previously found best parameters
# top_params = {'criterion': 'gini', 'n_estimators': 958, 'max_depth': 30, 'min_samples_split': 5, 'max_features': 'sqrt'}
# [I 2023-12-18 11:03:19,199] Trial 15 finished with value: 0.8129966329966329 and parameters: {'criterion': 'gini', 'n_estimators': 958, 'max_depth': 30, 'min_samples_split': 5, 'max_features': 'sqrt'}. Best is trial 15 with value: 0.8129966329966329.

# Train a model on the entire training dataset using the top parameters
final_model = RandomForestClassifier(**top_params, random_state=42, n_jobs=-1)
final_model.fit(x_train, ytrain.values.ravel())

# Make predictions on the test set
test_predictions = final_model.predict(x_validate)

# Optionally, evaluate the predictions
test_accuracy = accuracy_score(y_validate, test_predictions)
print(f'Test Accuracy: {test_accuracy}')

Test Accuracy: 0.8893939393939394


In [ ]:
# predictions = best_clf.predict(X_test)
import os
y_test = pd.read_csv('data\y_test.csv')
pred = pd.DataFrame(test_predictions, columns = [y_test.columns[1]])
del y_test['status_group']
y_test = pd.concat((y_test, pred), axis = 1)
y_test.to_csv(os.path.join('data', 'y_test101.csv'), sep=",", index = False)

#### XGBoost

In [58]:
import optuna
from xgboost import XGBClassifier
from sklearn.model_selection import cross_val_score

from sklearn.preprocessing import LabelEncoder

le = LabelEncoder()
ytrain_encoded = le.fit_transform(y_train.values.ravel())

def objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 750, 1250),
        'max_depth': trial.suggest_int('max_depth', 1, 12),
        'min_child_samples': trial.suggest_int('min_child_samples', 20, 70),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.5),
        'reg_lambda': trial.suggest_float('reg_lambda', 0, 10, step=0.5),
        'reg_alpha': trial.suggest_float('reg_alpha', 0, 10, step=0.5),
        'subsample': trial.suggest_float('subsample', 0.5, 1, step=0.05),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1, step=0.05),
        'gamma': trial.suggest_int('gamma', 0, 5),
        'max_bin': trial.suggest_int('max_bin', 50, 100),
        'objective': 'multi:softmax'
    }
    
    clf = XGBClassifier(**params)
    
    return cross_val_score(clf, x_train, ytrain_encoded, cv=2, verbose=1, scoring='accuracy').mean()

study2 = optuna.create_study(direction='maximize')
study2.optimize(objective, n_trials=50, n_jobs=-2)


[I 2024-09-25 16:32:30,236] A new study created in memory with name: no-name-7ec4aa6c-5c6f-4235-bf70-0dd3136c083d
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent work

In [59]:
print('Best trial: score {}, params {}'.format(study2.best_trial.value, study2.best_trial.params))

from sklearn.metrics import accuracy_score
top_params2 = study2.best_params

# Previously found best parameters
# [I 2023-12-18 11:03:19,199] Trial 15 finished with value: 0.8129966329966329 and parameters: {'criterion': 'gini', 'n_estimators': 958, 'max_depth': 30, 'min_samples_split': 5, 'max_features': 'sqrt'}. Best is trial 15 with value: 0.8129966329966329.
# [Parallel(n_jobs=-1)]: Using backend LokyBackend with 12 concurrent workers.

# Train a model on the entire training dataset using the top parameters
final_model2 = XGBClassifier(**top_params2, random_state=42, n_jobs=-1)
final_model2.fit(x_train, ytrain_encoded)

# Make predictions on the test set
test_predictions2 = final_model2.predict(x_validate)

# Optionally, evaluate the predictions
test_accuracy2 = accuracy_score(y_validate, test_predictions)
print(f'Test Accuracy: {test_accuracy2}')

Best trial: score 0.7934132996632997, params {'n_estimators': 825, 'max_depth': 8, 'min_child_samples': 36, 'learning_rate': 0.4408580704679031, 'reg_lambda': 7.0, 'reg_alpha': 8.0, 'subsample': 0.8500000000000001, 'colsample_bytree': 0.55, 'gamma': 0, 'max_bin': 50}


d:\Dev\Lib\site-packages\xgboost\core.py:160: UserWarning: [17:16:43] WARNING: C:\buildkite-agent\builds\buildkite-windows-cpu-autoscaling-group-i-0750514818a16474a-1\xgboost\xgboost-ci-windows\src\learner.cc:742: 
Parameters: { "min_child_samples" } are not used.

  warnings.warn(smsg, UserWarning)


Test Accuracy: 0.8893939393939394


In [ ]:
# predictions = best_clf.predict(X_test)
import os
y_test = pd.read_csv('data\y_test.csv')
decoded_predictions = le.inverse_transform(test_predictions2)
pred = pd.DataFrame(decoded_predictions, columns = [y_test.columns[1]])
del y_test['status_group']
y_test = pd.concat((y_test, pred), axis = 1)
y_test.to_csv(os.path.join('data', 'y_test102.csv'), sep=",", index = False)

#### CatBoost

In [62]:
from catboost import CatBoostClassifier
from sklearn.model_selection import cross_val_score
import optuna

def objective(trial):
    params = {
        'iterations': trial.suggest_int('iterations', 750, 1250),
        # 'n_estimators': trial.suggest_int('n_estimators', 750, 1250),
        'max_depth': trial.suggest_int('max_depth', 2, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'random_strength': trial.suggest_int('random_strength', 0, 100),
        'bagging_temperature': trial.suggest_float('bagging_temperature', 0.0, 1.0),
        'od_type': trial.suggest_categorical('od_type', ['IncToDec', 'Iter']),
        'od_wait': trial.suggest_int('od_wait', 10, 50),
        'max_bin': trial.suggest_int('max_bin', 50, 100)
    }
    
    clf = CatBoostClassifier(**params, verbose=1)
    
    return cross_val_score(clf, x_train, y_train.values.ravel(), cv=2, scoring='accuracy').mean()

study3 = optuna.create_study(direction='maximize')
study3.optimize(objective, n_trials=50, n_jobs=10)

print('Best trial: score {}, params {}'.format(study3.best_trial.value, study3.best_trial.params))

[I 2024-09-25 17:28:27,487] A new study created in memory with name: no-name-6147c16e-50c1-4b92-a147-63ff7134e57d


0:	learn: 1.0321821	total: 273ms	remaining: 4m 30s
0:	learn: 1.0538078	total: 354ms	remaining: 5m 36s
0:	learn: 1.0424228	total: 298ms	remaining: 5m 36s
0:	learn: 0.9505142	total: 281ms	remaining: 5m 3s
0:	learn: 1.0103642	total: 461ms	remaining: 6m 35s
1:	learn: 0.8787671	total: 327ms	remaining: 2m 56s
1:	learn: 0.9642685	total: 496ms	remaining: 3m 32s
1:	learn: 1.0086351	total: 421ms	remaining: 3m 20s
0:	learn: 1.0569662	total: 20ms	remaining: 16.9s
2:	learn: 0.9814540	total: 443ms	remaining: 2m 20s
1:	learn: 0.9893021	total: 332ms	remaining: 3m 7s
1:	learn: 0.9872549	total: 326ms	remaining: 2m 41s
2:	learn: 0.9251681	total: 549ms	remaining: 2m 36s
0:	learn: 1.0293834	total: 24.1ms	remaining: 18.4s
2:	learn: 0.8382579	total: 384ms	remaining: 2m 17s
1:	learn: 1.0242465	total: 60ms	remaining: 25.3s
2:	learn: 0.9505969	total: 364ms	remaining: 2m
2:	learn: 0.9531456	total: 372ms	remaining: 2m 19s
3:	learn: 0.9463115	total: 491ms	remaining: 1m 56s
1:	learn: 0.9681983	total: 48ms	remaining

[I 2024-09-25 17:29:02,551] Trial 6 finished with value: 0.7792508417508417 and parameters: {'iterations': 764, 'max_depth': 3, 'learning_rate': 0.22191814222752515, 'random_strength': 23, 'bagging_temperature': 0.532719309869351, 'od_type': 'IncToDec', 'od_wait': 27, 'max_bin': 98}. Best is trial 6 with value: 0.7792508417508417.


717:	learn: 0.3650102	total: 33.2s	remaining: 6.53s
663:	learn: 0.4611082	total: 32s	remaining: 26.5s
979:	learn: 0.5271819	total: 32.8s	remaining: 435ms
870:	learn: 0.5198793	total: 33s	remaining: 3.1s
724:	learn: 0.4816406	total: 32.8s	remaining: 18.4s
113:	learn: 0.6815057	total: 3.26s	remaining: 20.9s
740:	learn: 0.3429307	total: 33.1s	remaining: 15.2s
payment_pay monthly, bin=0 score 3.383750483
population, bin=3 score 3.380401821
235:	learn: 0.5994772	total: 33.4s	remaining: 1m 48s
980:	learn: 0.5271207	total: 32.8s	remaining: 401ms
quantity_seasonal, bin=0 score 4.688030456


871:	learn: 0.5198224	total: 33s	remaining: 3.06s
725:	learn: 0.4815051	total: 32.8s	remaining: 18.3s

district_code_1, bin=0 score 3.947620741

funder_concern world wide, bin=0 score 0.6276069387

source_machine dbh, bin=0 score 0.9971122389
subvillage_majengo, bin=0 score 15.58631446
ward_ihanda, bin=0 score 1.054533124
funder_roman catholic, bin=0 score 1.630557336
664:	learn: 0.4609565	total: 32.1s	rema

[I 2024-09-25 17:29:26,952] Trial 5 finished with value: 0.7623106060606061 and parameters: {'iterations': 846, 'max_depth': 2, 'learning_rate': 0.12677143349226025, 'random_strength': 47, 'bagging_temperature': 0.129115390749024, 'od_type': 'IncToDec', 'od_wait': 33, 'max_bin': 59}. Best is trial 6 with value: 0.7792508417508417.


...

[I 2024-09-25 17:52:46,844] Trial 43 finished with value: 0.7966119528619529 and parameters: {'iterations': 1143, 'max_depth': 8, 'learning_rate': 0.12611528613532186, 'random_strength': 89, 'bagging_temperature': 0.5724527380392078, 'od_type': 'Iter', 'od_wait': 36, 'max_bin': 75}. Best is trial 27 with value: 0.7976641414141414.


gps_height, bin=22 score 2.785682005


[I 2024-09-25 17:52:56,793] Trial 45 finished with value: 0.7941287878787879 and parameters: {'iterations': 967, 'max_depth': 8, 'learning_rate': 0.14376606564895358, 'random_strength': 61, 'bagging_temperature': 0.5652969447509207, 'od_type': 'Iter', 'od_wait': 28, 'max_bin': 75}. Best is trial 27 with value: 0.7976641414141414.
[I 2024-09-25 17:53:19,153] Trial 44 finished with value: 0.7967171717171717 and parameters: {'iterations': 1140, 'max_depth': 8, 'learning_rate': 0.14196279692216365, 'random_strength': 62, 'bagging_temperature': 0.5744288135382767, 'od_type': 'Iter', 'od_wait': 40, 'max_bin': 77}. Best is trial 27 with value: 0.7976641414141414.


[I 2024-09-25 17:53:19,257] Trial 40 finished with value: 0.7958964646464646 and parameters: {'iterations': 1126, 'max_depth': 10, 'learning_rate': 0.08075514556661337, 'random_strength': 62, 'bagging_temperature': 0.5854046600113317, 'od_type': 'Iter', 'od_wait': 36, 'max_bin': 86}. Best is trial 27 with value: 0.7976641414141414.
[I 2024-09-25 17:53:32,707] Trial 46 finished with value: 0.7954545454545454 and parameters: {'iterations': 1141, 'max_depth': 8, 'learning_rate': 0.1420666372918805, 'random_strength': 88, 'bagging_temperature': 0.5774632861900331, 'od_type': 'Iter', 'od_wait': 34, 'max_bin': 86}. Best is trial 27 with value: 0.7976641414141414.
[I 2024-09-25 17:53:37,115] Trial 47 finished with value: 0.7964436026936026 and parameters: {'iterations': 1144, 'max_depth': 8, 'learning_rate': 0.1380191116381684, 'random_strength': 62, 'bagging_temperature': 0.5926761378268766, 'od_type': 'Iter', 'od_wait': 29, 'max_bin': 86}. Best is trial 27 with value: 0.7976641414141414.
[I

Best trial: score 0.7976641414141414, params {'iterations': 1073, 'max_depth': 10, 'learning_rate': 0.084778945186221, 'random_strength': 69, 'bagging_temperature': 0.4717755636425249, 'od_type': 'IncToDec', 'od_wait': 37, 'max_bin': 80}


In [64]:
print('Best trial: score {}, params {}'.format(study3.best_trial.value, study3.best_trial.params))

from sklearn.metrics import accuracy_score
top_params3 = study3.best_params

# Previously found best parameters
# [I 2023-12-18 11:03:19,199] Trial 15 finished with value: 0.8129966329966329 and parameters: {'criterion': 'gini', 'n_estimators': 958, 'max_depth': 30, 'min_samples_split': 5, 'max_features': 'sqrt'}. Best is trial 15 with value: 0.8129966329966329.
# [Parallel(n_jobs=-1)]: Using backend LokyBackend with 12 concurrent workers.

# Train a model on the entire training dataset using the top parameters
final_model3 = CatBoostClassifier(**top_params3, random_state=42)
final_model3.fit(x_train, y_train)

# Make predictions on the test set
test_predictions3 = final_model3.predict(x_validate)

# Optionally, evaluate the predictions
test_accuracy3 = accuracy_score(y_validate, test_predictions3)
print(f'Test Accuracy: {test_accuracy3}')

Best trial: score 0.7976641414141414, params {'iterations': 1073, 'max_depth': 10, 'learning_rate': 0.084778945186221, 'random_strength': 69, 'bagging_temperature': 0.4717755636425249, 'od_type': 'IncToDec', 'od_wait': 37, 'max_bin': 80}
0:	learn: 1.0625036	total: 64.1ms	remaining: 1m 8s
1:	learn: 1.0201838	total: 127ms	remaining: 1m 7s
2:	learn: 0.9924759	total: 168ms	remaining: 1m
3:	learn: 0.9634362	total: 225ms	remaining: 1m
4:	learn: 0.9348844	total: 287ms	remaining: 1m 1s
5:	learn: 0.9097769	total: 345ms	remaining: 1m 1s
6:	learn: 0.8964112	total: 405ms	remaining: 1m 1s
7:	learn: 0.8754043	total: 464ms	remaining: 1m 1s
8:	learn: 0.8582105	total: 524ms	remaining: 1m 1s
9:	learn: 0.8482128	total: 580ms	remaining: 1m 1s
10:	learn: 0.8363971	total: 640ms	remaining: 1m 1s
11:	learn: 0.8209202	total: 699ms	remaining: 1m 1s
12:	learn: 0.8122935	total: 759ms	remaining: 1m 1s
13:	learn: 0.7989260	total: 817ms	remaining: 1m 1s
14:	learn: 0.7916614	total: 874ms	remaining: 1m 1s
15:	learn: 0

In [ ]:
import os
y_test = pd.read_csv(r'D:\MMAI\Pump-It-Up\data\y_test.csv')
pred = pd.DataFrame(test_predictions3, columns = [y_test.columns[1]])
del y_test['status_group']
y_test = pd.concat((y_test, pred), axis = 1)
y_test.to_csv(os.path.join('data', 'y_test102.csv'), sep=",", index = False)

### Ensemble Voting

In [ ]:
import pandas as pd
from scipy.stats import mode

# Load the prediction files
y_test_RF = pd.read_csv('data/y_test_RF.csv')
y_test_XG = pd.read_csv('data/y_test_XG.csv')
y_test_Cat = pd.read_csv('data/y_test_Cat.csv')

# Extract the predictions
pred_RF = y_test_RF['status_group']
pred_XG = y_test_XG['status_group']
pred_Cat = y_test_Cat['status_group']

# Perform majority voting
majority_vote = mode([pred_RF, pred_XG, pred_Cat])[0][0]

# Create a new DataFrame for the majority vote predictions
majority_vote_df = pd.DataFrame(majority_vote, columns=['status_group'])

# Add the 'id' field from the original dataframes
majority_vote_df['id'] = pred_RF['id']

# Rearrange the columns to make 'id' the first column
majority_vote_df = majority_vote_df.reindex(columns=['id', 'status_group'])

# Save the majority vote predictions to a CSV file
majority_vote_df.to_csv('data/y_test_majority_vote.csv', index=False)

C:\Users\Namsi\AppData\Local\Temp\ipykernel_9328\327996402.py:15: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  majority_vote = mode([preds100, preds101, preds102])[0][0]
C:\Users\Namsi\AppData\Local\Temp\ipykernel_9328\327996402.py:15: DeprecationWarning: Support for non-numeric arrays has been deprecated as of SciPy 1.9.0 and will be removed in 1.11.0. `pandas.DataFrame.mode` can be used instead, see https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.mode.html.
  majority_vote = mode([preds100, preds101, preds102])[0][0]
